In [1]:
# 필요한 라이브러리를 import

import sys
import requests
import json
import pandas as pd
import itertools
import time
import math
import numpy as np
from flatten_dict import flatten
from flatten_dict.reducer import make_reducer
import matplotlib.pyplot as plt 
import seaborn as sns    
import torch
from torch.utils.data import  TensorDataset, DataLoader
from torch import nn, optim
import random
from glob import glob
import torch.optim as optimizer
from torch.optim.lr_scheduler import StepLR
from pathlib import Path
from tqdm import tqdm
import torch.nn.functional as F

# pandas - DataFrame의 크기를 모두 표시하도록 설정

pd.options.display.max_columns = None
pd.options.display.max_rows = None

use_cuda = torch.cuda.is_available()

# riot-API 이용을 위한 api-key값

api_key = 'RGAPI-99a660f1-04f1-459d-8aac-a7a0c2eeb34e'

# 각 tier별 game id를 가져오기 위해 url 저장

IRON_URL4='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/IRON/IV?page='
IRON_URL3='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/IRON/III?page='
IRON_URL2='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/IRON/II?page='
IRON_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/IRON/I?page='
BRONZE_URL4='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/BRONZE/IV?page='
BRONZE_URL3='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/BRONZE/III?page='
BRONZE_URL2='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/BRONZE/II?page='
BRONZE_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/BRONZE/I?page='
SILVER_URL4='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/SILVER/IV?page='
SILVER_URL3='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/SILVER/III?page='
SILVER_URL2='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/SILVER/II?page='
SILVER_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/SILVER/I?page='
GOLD_URL4='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/GOLD/IV?page='
GOLD_URL3='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/GOLD/III?page='
GOLD_URL2='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/GOLD/II?page='
GOLD_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/GOLD/I?page='
PLATINUM_URL4='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/PLATINUM/IV?page='
PLATINUM_URL3='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/PLATINUM/III?page='
PLATINUM_URL2='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/PLATINUM/II?page='
PLATINUM_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/PLATINUM/I?page='
DIAMOND_URL4='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/DIAMOND/IV?page='
DIAMOND_URL3='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/DIAMOND/III?page='
DIAMOND_URL2='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/DIAMOND/II?page='
DIAMOND_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/DIAMOND/I?page='
MASTER_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/MASTER/I?page='
GRANDMASTER_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/GRANDMASTER/I?page='
CHALLENGER_URL1='https://kr.api.riotgames.com/lol/league-exp/v4/entries/RANKED_SOLO_5x5/CHALLENGER/I?page='

# match의 정보를 가져오기 위한 url저장
MATCH_URL = 'https://kr.api.riotgames.com/lol/match/v4/matches/'


def gameIdLoader(path, api_key):
    gameIds = np.load(path)
    matches=[]
    a = 0
    for i in tqdm(gameIds):
        # request limit( 20 requests every 1 seconds(s) , 100 requests every 2 minutes(s) )에 대한 해결 방안으로 time.sleep 을 120이상으로 설정
        if a % 20 == 0:
            time.sleep(2)
        if a % 100 == 0:
            time.sleep(125)
        load_url = MATCH_URL + str(i)
        res = requests.get(load_url, headers={"X-Riot-Token": api_key})
        ob=json.loads(res.text)
        if 'gameDuration' in ob:
            if ob['gameMode'] != 'CLASSIC':
                a += 1
                continue
            matches.append(ob)
        else:
            print(ob)
            print("-Error recovery time-")
            time.sleep(90)
            rest=gameIdLoaderRe([i], api_key)
            matches.append(rest[0])
            print("-Error fixed-")
        a += 1
    return matches
    
    
def gameIdLoaderRe(gameIds, api_key):
    matches=[]
    for i in tqdm(gameIds):
        load_url = MATCH_URL + str(i)
        res = requests.get(load_url, headers={"X-Riot-Token": api_key})
        ob=json.loads(res.text)
        if 'gameDuration' in ob:
            matches.append(ob)
        else:
            print(ob)
            print("-Error recovery time-")
            time.sleep(90)
            rest=gameIdLoaderRe([i], api_key)
            matches.append(rest[0])
            print("-Error fixed-")
    return matches
    
    
def flatter(matches):
    matchlist = []
    for i in matches:
        matchlist.append(flatten(i, enumerate_types=(list,), reducer=make_reducer(delimiter='_')))
    
    return matchlist


def filter_dict(d, f):
    ''' Filters dictionary d by function f. '''
    newDict = dict()
    # Iterate over all (k,v) pairs in names
    for key, value in d.items():
        # Is condition satisfied?
        if f(key, value):
            newDict[key] = value
    return newDict


def filter_team_dict(d, f):
    ''' Filters dictionary d by function f. '''
    newDict = dict()
    # Iterate over all (k,v) pairs in names
    ind = -1
    kl = ['teams_win', 'teams_firstBlood', 'teams_firstTower', 'teams_firstInhibitor', 'teams_firstBaron', 'teams_firstDragon', 'teams_firstRiftHerald', 'teams_towerKills', 'teams_inhibitorKills', 'teams_baronKills', 'teams_dragonKills', 'teams_riftHeraldKills']
    for key, value in d.items():
        # Is condition satisfied?
        if f(key, value):
            ind += 1
            newDict[kl[ind]] = value
    return newDict


def filter_participant_dict(d, f):
    ''' Filters dictionary d by function f. '''
    newDict = dict()
    # Iterate over all (k,v) pairs in names
    for key, value in d.items():
        # Is condition satisfied?
        if f(key, value):
            pkey = 'total_'+key[14:]
            newDict[pkey] = value
    return newDict


def winTeams_0(match):
    matchtemp = match
    
    for delstring in ['item', 'Id', 'playerScore', 'perk', 'Perk', 'bans', 'PlayerScore', 'timeline_csDiffPerMinDeltas_0-10', 'stats_totalScoreRank', 'dominionVictoryScore', 'stats_win', 'stats_unrealKills', 'stats_sightWardsBoughtInGame', 'timeline', 'vilemawKills', 'dominionVictoryScore','stats_firstInhibitorAssist','stats_firstInhibitorKill', 'stats_firstTowerAssist', 'stats_firstTowerKill', 'stats_firstBloodAssist', 'stats_firstBloodKill','turretKills','towerKills', 'damageDealtToTurrets']: 
        temp = list(filter_dict(match, lambda k,v: delstring in k).keys())
        for i in temp:
            del(matchtemp[i])
    
    
    avg_data = (np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_0' in k).values())) 
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_1' in k).values())) 
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_2' in k).values())) 
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_3' in k).values()))
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_4' in k).values())))
    avg_label = list(filter_participant_dict(matchtemp, lambda k,v: 'participants_0' in k).keys())
    win = {avg_label[i]: avg_data[i] for i in range(len(avg_label))}
    
    
    avg_data = (np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_5' in k).values())) 
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_6' in k).values())) 
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_7' in k).values())) 
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_8' in k).values()))
    + np.array(list(filter_participant_dict(matchtemp, lambda k,v: 'participants_9' in k).values())))
    loss = {avg_label[i]: avg_data[i] for i in range(len(avg_label))}
    
    win.update(filter_team_dict(matchtemp, lambda k,v: 'teams_0' in k))
    loss.update(filter_team_dict(matchtemp, lambda k,v: 'teams_1' in k))
    
    return [win, loss]


def winTeams_1(match):
    temp = winTeams_0(match)
    return [temp[1], temp[0]]


def divideTeams(matches):
    resultList = list()
    for i in matches:
        lossDict = dict()
        winDict = dict()
        lossDict.update({'gameDuration':i['gameDuration']})
        winDict.update({'gameDuration':i['gameDuration']})
        lossDict.update({'gameMode':i['gameMode']})
        winDict.update({'gameMode':i['gameMode']})
        
        if i['teams_0_win'] == 'Win':
            winDict.update(winTeams_0(i)[0])
            lossDict.update(winTeams_0(i)[1])
        else:
            winDict.update(winTeams_1(i)[0])
            lossDict.update(winTeams_1(i)[1])
        resultList.append(winDict)
        resultList.append(lossDict)
    return resultList   


def preprocessing(matches):
    df = pd.DataFrame(divideTeams(flatter(matches)))
    df["teams_firstBlood"] = df["teams_firstBlood"].astype(int)
    df["teams_firstTower"] = df["teams_firstTower"].astype(int)
    df["teams_firstInhibitor"] = df["teams_firstInhibitor"].astype(int)
    df["teams_firstBaron"] = df["teams_firstBaron"].astype(int)
    df["teams_firstDragon"] = df["teams_firstDragon"].astype(int)
    df["teams_firstRiftHerald"] = df["teams_firstRiftHerald"].astype(int)
    df.insert(0, 'team_win', df.teams_win)
    df = df.drop(columns=['teams_win', 'gameMode'])
    df['team_win'] = df['team_win'].replace(['Win','Fail'],[10000,-500])
    return df


def getDataFrame(path, api_key):
    return preprocessing(gameIdLoader(path, api_key))

In [2]:
df_diamond = getDataFrame('gameId/diamond/diamond_3_gameId_1.npy', api_key)
df3 = getDataFrame('gameId/diamond/diamond_2_gameId_1.npy', api_key)
df4 = getDataFrame('gameId/diamond/diamond_4_gameId_1.npy', api_key)

df_diamond = df_diamond.append(df3)
df_diamond = df_diamond.append(df4)
df_diamond.to_csv("dataFrame/diamond.csv")

 95%|████████████████████████████████████████████████████████████████████████████    | 380/400 [11:14<00:06,  2.87it/s]

{'status': {'message': 'Gateway timeout', 'status_code': 504}}
-Error recovery time-



 95%|████████████████████████████████████████████████████████████████████████████▏   | 381/400 [12:47<08:52, 28.05s/it]

-Error fixed-


100%|████████████████████████████████████████████████████████████████████████████████| 400/400 [11:19<00:00,  1.70s/it]


In [3]:
df_over_diamond = getDataFrame('gameId/diamond/diamond_1_gameId_1.npy', api_key)
df2 = getDataFrame('gameId/master/master_gameId_1.npy', api_key)
df1 = getDataFrame('gameId/grandmaster/grandmaster_gameId_1.npy', api_key)
df0 = getDataFrame('gameId/challenger/challenger_gameId_1.npy', api_key)


df_over_diamond = df_over_diamond.append(df0)
df_over_diamond = df_over_diamond.append(df1)
df_over_diamond = df_over_diamond.append(df2)

df_over_diamond.to_csv("dataFrame/over_diamond.csv")


  8%|██████▎                                                                          | 31/400 [02:19<02:10,  2.83it/s]

{'status': {'message': 'Gateway timeout', 'status_code': 504}}
-Error recovery time-



  8%|██████▎                                                                        | 32/400 [03:50<2:48:35, 27.49s/it]

-Error fixed-


 42%|██████████████████████████████████                                              | 170/400 [07:02<01:27,  2.62it/s]

...

 68%|██████████████████████████████████████████████████████▌                         | 124/182 [05:07<00:32,  1.78it/s]

{'status': {'message': 'Gateway timeout', 'status_code': 504}}
-Error recovery time-



 69%|██████████████████████████████████████████████████████▉                         | 125/182 [06:37<26:14, 27.63s/it]

-Error fixed-


100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [02:54<00:00,  1.74s/it]


In [5]:
df_over_diamond

team_win  gameDuration  total__stats_kills  total__stats_deaths  \
0       10000          1584                  24                   22   
1        -500          1584                  22                   24   
2       10000          2141                  48                   40   
3        -500          2141                  40                   48   
4       10000          1516                  33                   21   
5        -500          1516                  21                   33   
6       10000          1281                  23                    9   
7        -500          1281                   9                   23   
8       10000          1518                  32                   17   
9        -500          1518                  17                   32   
10      10000           776                  21                    3   
11       -500           776                   3                   21   
12      10000          1976                  42                   30   
13       -500          1976                  30                   42   
14      10000           922                  23                   10   
15       -500           922                  10                   23   
16      10000          1465                  30                   21   
17       -500          1465                  21                   30   
18      10000          1483                  32                   19   
19       -500          1483                  19                   32   
20      10000          1586                  34                   18   
21       -500          1586                  18                   34   
22      10000          1712                  45                   26   
23       -500          1712                  26                   45   
24      10000          2172                  41                   39   
25       -500          2172                  39                   41   
26      10000           662                  12                    7   
27       -500           662                   7                   12   
28      10000           949                  31                    5   
29       -500           949                   5                   31   
30      10000          1640                  27                   14   
31       -500          1640                  14                   27   
32      10000          2112                  26                   38   
33       -500          2112                  38                   27   
34      10000          1512                  31                   17   
35       -500          1512                  17                   31   
36      10000          2173                  42                   37   
37       -500          2173                  37                   42   
38      10000          1199                  26                   11   
39       -500          1199                  11                   27   
40      10000          2218                  37                   34   
41       -500          2218                  34                   37   
42      10000          1935                  25                   15   
43       -500          1935                  15                   25   
44      10000          1924                  34                   16   
45       -500          1924                  16                   34   
46      10000          1784                  39                   25   
47       -500          1784                  25                   39   
48      10000          1497                  34                   19   
49       -500          1497                  19                   34   
50      10000          2256                  41                   30   
51       -500          2256                  30                   41   
52      10000          1075                  18                    7   
53       -500          1075                   7                   18   
54      10000          1939                  